# Enrich station data with distances

In [186]:
import glob
import re
import math
import json
import pandas as pd
import numpy as np
import plotly.express as px

# Joshuas nice little helper function

def get_distance(lat1, lon1, lat2, lon2):
    R = 6371  # Radius of the Earth in kilometers
    lat1, lon1, lat2, lon2 = map(math.radians, [lat1, lon1, lat2, lon2])
    dlat = lat2 - lat1
    dlon = lon2 - lon1
    a = math.sin(dlat/2)**2 + math.cos(lat1) * math.cos(lat2) * math.sin(dlon/2)**2
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1-a))
    return R * c


In [21]:
# 1. collect all stations from a given time period (start with 1 week) with master data:
#
# columns to take over:
#    - uuid,name,brand,street,house_number,post_code,city,latitude,longitude
#
# columns to create
#   - first_seen: date where station occurred first
#   - last_seen: date where station occurred last

work_dir = "data/stations/2023/05"
station_files = glob.glob(work_dir + "/*.csv")
station_list = pd.DataFrame()

for filename in station_files:
    current_file = pd.read_csv(filename)
    current_file["file_date"] = re.search("[\d]{4}-[\d]{2}-[\d]{2}",filename).group()
    station_list = pd.concat([station_list, current_file])

station_list["file_date"] = pd.to_datetime(station_list["file_date"])

# extract only basic info for calculation
station_location = station_list[["uuid", "longitude", "latitude"]].copy()




# 2. calculate spatial distance between stations
#
# do it for one single station first


# 3. retrieve driving distance
#    (and in the same turn probably driving time)

In [57]:
# build a UUID x UUID matrix to fill up with distances later

station_matrix = station_location.copy()

# CAUTION: we may have UUIDs with differing lat, lon info
#          will drop dups for now - HAVE TO TAKE CARE
station_matrix.drop_duplicates(subset="uuid" ,inplace=True)
uuid_list = station_matrix["uuid"]

for uuid in uuid_list:
    station_matrix[uuid] = 0

station_matrix.set_index("uuid", inplace=True)

/var/folders/zg/k61cnpxd5b56kl16rcs2_3sc0000gn/T/ipykernel_43671/3241753199.py:11: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`

/var/folders/zg/k61cnpxd5b56kl16rcs2_3sc0000gn/T/ipykernel_43671/3241753199.py:11: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`

/var/folders/zg/k61cnpxd5b56kl16rcs2_3sc0000gn/T/ipykernel_43671/3241753199.py:11: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd

In [231]:
# helper: reset dataframe

#station_distances = station_matrix.copy()
station_distances = station_matrix

uuid_cols = list(station_distances.columns)
uuid_cols.remove("longitude")
uuid_cols.remove("latitude")
for col in uuid_cols:
    station_distances[col].values[:] = 0


In [233]:
# calculate distances for a single test_station

#test_station = uuid_list[0]

# to test just do it until c == 100
c = 0
for start in uuid_list:
    c += 1
    print("Station #" + str(c))
    #if c == 100: break
    
    for destination in uuid_list:
        start_lat = station_distances.loc[start, "latitude"]
        start_lon = station_distances.loc[start, "longitude"]
        dest_lat = station_distances.loc[destination, "latitude"]
        dest_lon = station_distances.loc[destination, "longitude"]

        if station_distances.loc[start, destination] == 0:
            distance = get_distance(start_lat, start_lon, dest_lat, dest_lon)
            station_distances.loc[start, destination] = distance
            station_distances.loc[destination, start] = distance




Station #1
Station #2
Station #3
Station #4
Station #5
Station #6
Station #7
Station #8
Station #9
Station #10
Station #11
Station #12
Station #13
Station #14
Station #15
Station #16
Station #17
Station #18
Station #19
Station #20
Station #21
Station #22
Station #23
Station #24
Station #25
Station #26
Station #27
Station #28
Station #29
Station #30
Station #31
Station #32
Station #33
Station #34
Station #35
Station #36
Station #37
Station #38
Station #39
Station #40
Station #41
Station #42
Station #43
Station #44
Station #45
Station #46
Station #47
Station #48
Station #49
Station #50
Station #51
Station #52
Station #53
Station #54
Station #55
Station #56
Station #57
Station #58
Station #59
Station #60
Station #61
Station #62
Station #63
Station #64
Station #65
Station #66
Station #67
Station #68
Station #69
Station #70
Station #71
Station #72
Station #73
Station #74
Station #75
Station #76
Station #77
Station #78
Station #79
Station #80
Station #81
Station #82
Station #83
Station #84
S

: 

: 

In [172]:
### test openrouteservice.org ###
#
# first test: 
# - take one station
# - get the 49 nearest stations (linear distance)
# - build lat/lon array of the 50 stations
# - call the "matrix" endpoint from openrouteservice.org
# - process the response JSON and fill in the time distance for the pairs

test_station = uuid_list[0]

distance_sort = station_distances[test_station].sort_values()
nearest_stations = distance_sort[:50]
all_stations = station_location.copy()
all_stations.set_index("uuid", inplace=True)
nearest_stations = nearest_stations.to_frame().merge(all_stations, left_index=True, right_index=True)
lonlat_pairs = nearest_stations[["longitude","latitude"]].to_numpy()

In [179]:
type(lonlat_pairs)
myarray = lonlat_pairs.tolist()
myarray

[[9.2790394, 50.7520089],
 [9.2774664, 50.75223],
 [9.285781, 50.751505],
 [9.26297, 50.74686],
 [9.26342, 50.74624],
 [9.259057, 50.744035],
 [9.24696, 50.73821],
 [9.241473, 50.733436],
 [9.359395, 50.760316],
 [9.40501, 50.76294],
 [9.28796, 50.8387],
 [9.40995, 50.81634],
 [9.219599, 50.851036],
 [9.219599, 50.85104],
 [9.108746, 50.76683],
 [9.397970199585, 50.668899536133],
 [9.351511, 50.863052],
 [9.33628, 50.8721],
 [9.337172, 50.871994],
 [9.47747, 50.74185],
 [9.394659, 50.642291],
 [9.39447, 50.6379],
 [9.406314, 50.641471],
 [9.41035, 50.6403],
 [9.3966, 50.6314],
 [9.10986, 50.8523],
 [9.107086, 50.851162],
 [9.23354, 50.90667],
 [9.4401372, 50.631116],
 [9.46667, 50.85773],
 [9.46721251, 50.8576193],
 [9.249208, 50.91245],
 [9.2410497665405, 50.91296005249],
 [9.2388573, 50.912961],
 [9.24068, 50.9132],
 [9.19948, 50.9094],
 [9.264897, 50.58261],
 [9.206124, 50.9180137],
 [9.038366, 50.8352623],
 [9.09017, 50.62064],
 [9.0902595520019, 50.620559692383],
 [9.2494020462036

In [189]:
# doing the API call to openrouteservice.org
# REMOVE KEY BEFORE GOING PUBLIC - has to be in .env with gitignore
import openrouteservice as ors
ors_client = ors.Client(key="5b3ce3597851110001cf6248e825fff72a3348c99489a2c4097ee2f9")
ors_response = ors_client.distance_matrix(lonlat_pairs.tolist(),
                                             profile="driving-car",
                                             resolve_locations=True)

--- 

# Debugging Area


---

In [197]:
distance_string = json.dumps(ors_response)
distance_json = json.loads(distance_string)
print(distance_json["durations"])

[[0.0, 17.34, 68.2, 200.15, 207.36, 249.36, 329.94, 372.59, 796.66, 643.56, 718.84, 976.63, 1034.33, 1034.36, 934.89, 928.13, 1071.54, 1174.34, 1160.04, 1007.65, 961.74, 987.13, 1042.93, 1096.44, 1113.28, 1473.98, 1488.93, 1334.22, 1254.78, 1468.4, 1457.6, 1380.05, 1463.19, 1490.3, 1466.15, 1476.27, 1487.39, 1607.42, 1812.48, 1429.25, 1428.2, 1732.36, 1708.64, 1752.61, 2030.72, 1501.76, 1873.67, 2027.99, 1526.72, 1079.77], [17.34, 0.0, 85.5, 190.59, 197.81, 239.8, 338.83, 389.89, 813.96, 660.85, 736.14, 993.93, 1024.77, 1024.81, 925.34, 945.43, 1088.84, 1191.63, 1177.34, 1024.95, 979.03, 1004.42, 1060.22, 1113.73, 1130.58, 1464.43, 1479.38, 1351.52, 1272.07, 1485.69, 1474.89, 1397.35, 1480.48, 1507.59, 1483.45, 1466.71, 1504.69, 1597.87, 1802.92, 1446.55, 1445.5, 1749.66, 1699.08, 1743.06, 2021.17, 1492.2, 1864.11, 2018.43, 1544.02, 1097.06], [80.98, 98.27, 0.0, 281.08, 288.3, 328.94, 280.68, 323.33, 747.4, 594.3, 669.58, 927.37, 1039.44, 1039.4, 1015.83, 872.75, 1022.28, 1125.08, 1110

In [198]:
distance_matrix = pd.DataFrame(distance_json["durations"])

In [209]:
distance_matrix.iloc[25,47]

559.97

In [230]:
distance_matrix.iloc[48:52,0:1]

0
48  1545.02
49  1066.31

In [184]:
driving_time = pd.DataFrame(distance_matrix{"durations"})


SyntaxError: invalid syntax. Perhaps you forgot a comma? (445417096.py, line 1)

In [202]:
distance_json

{'durations': [[0.0,
   17.34,
   68.2,
   200.15,
   207.36,
   249.36,
   329.94,
   372.59,
   796.66,
   643.56,
   718.84,
   976.63,
   1034.33,
   1034.36,
   934.89,
   928.13,
   1071.54,
   1174.34,
   1160.04,
   1007.65,
   961.74,
   987.13,
   1042.93,
   1096.44,
   1113.28,
   1473.98,
   1488.93,
   1334.22,
   1254.78,
   1468.4,
   1457.6,
   1380.05,
   1463.19,
   1490.3,
   1466.15,
   1476.27,
   1487.39,
   1607.42,
   1812.48,
   1429.25,
   1428.2,
   1732.36,
   1708.64,
   1752.61,
   2030.72,
   1501.76,
   1873.67,
   2027.99,
   1526.72,
   1079.77],
  [17.34,
   0.0,
   85.5,
   190.59,
   197.81,
   239.8,
   338.83,
   389.89,
   813.96,
   660.85,
   736.14,
   993.93,
   1024.77,
   1024.81,
   925.34,
   945.43,
   1088.84,
   1191.63,
   1177.34,
   1024.95,
   979.03,
   1004.42,
   1060.22,
   1113.73,
   1130.58,
   1464.43,
   1479.38,
   1351.52,
   1272.07,
   1485.69,
   1474.89,
   1397.35,
   1480.48,
   1507.59,
   1483.45,
   1466.71,
  

In [24]:
station_location.drop_duplicates(subset="uuid" ,inplace=True)
#station_list[["uuid","latitude","longitude"]].groupby("uuid").head(100)

In [25]:
station_location.shape

(16885, 3)

In [26]:
station_location.uuid.nunique()

16885

In [27]:
station_list.shape

(168775, 12)

In [227]:
station_list.query("longitude == 9.2790394")

uuid            name brand          street   
0  44e2bdb7-13e3-4156-8576-8326cdd20459  bft Tankstelle   NaN  Schellengasse   \
1  44e2bdb7-13e3-4156-8576-8326cdd20459  bft Tankstelle   NaN  Schellengasse    
0  44e2bdb7-13e3-4156-8576-8326cdd20459  bft Tankstelle   NaN  Schellengasse    
1  44e2bdb7-13e3-4156-8576-8326cdd20459  bft Tankstelle   NaN  Schellengasse    
0  44e2bdb7-13e3-4156-8576-8326cdd20459  bft Tankstelle   NaN  Schellengasse    
0  44e2bdb7-13e3-4156-8576-8326cdd20459  bft Tankstelle   NaN  Schellengasse    
1  44e2bdb7-13e3-4156-8576-8326cdd20459  bft Tankstelle   NaN  Schellengasse    
1  44e2bdb7-13e3-4156-8576-8326cdd20459  bft Tankstelle   NaN  Schellengasse    
0  44e2bdb7-13e3-4156-8576-8326cdd20459  bft Tankstelle   NaN  Schellengasse    
0  44e2bdb7-13e3-4156-8576-8326cdd20459  bft Tankstelle   NaN  Schellengasse    

  house_number post_code     city   latitude  longitude   
0           53     36304  Alsfeld  50.752009   9.279039  \
1           53     36304  Alsfeld  50.752009   9.279039   
0           53     36304  Alsfeld  50.752009   9.279039   
1           53     36304  Alsfeld  50.752009   9.279039   
0           53     36304  Alsfeld  50.752009   9.279039   
0           53     36304  Alsfeld  50.752009   9.279039   
1           53     36304  Alsfeld  50.752009   9.279039   
1           53     36304  Alsfeld  50.752009   9.279039   
0           53     36304  Alsfeld  50.752009   9.279039   
0           53     36304  Alsfeld  50.752009   9.279039   

             first_active openingtimes_json  file_date  
0  1970-01-01 01:00:00+01                {} 2023-05-06  
1  1970-01-01 01:00:00+01                {} 2023-05-01  
0  1970-01-01 01:00:00+01                {} 2023-05-07  
1  1970-01-01 01:00:00+01                {} 2023-05-09  
0  1970-01-01 01:00:00+01                {} 2023-05-08  
0  1970-01-01 01:00:00+01                {} 2023-05-05  
1  1970-01-01 01:00:00+01                {} 2023-05-02  
1  1970-01-01 01:00:00+01                {} 2023-05-10  
0  1970-01-01 01:00:00+01                {} 2023-05-03  
0  1970-01-01 01:00:00+01                {} 2023-05-04

In [144]:
# check if transposed cells after the first 100 stations have been filled, too
station_matrix.loc[station_location["uuid"].loc[95:105]]

longitude   latitude   
uuid                                                         
64d12df3-2339-4d01-87a5-730663b6e9d5  10.336607  48.754295  \
64d208c2-6e07-48eb-8824-1237ab1a3ab3   8.893157  53.111651   
dfe3bd39-83cd-43b9-8628-f09896331b19   9.268370  48.804750   
10dbb42c-f2bb-5985-9dad-fbce82794a46   9.992393  53.468426   
dfcd38b3-602f-4d88-bb2f-f169c7176ea6  11.018116  49.419667   
64d9e72f-6327-4257-98bd-d0fbe75d4eee   9.513178  48.713700   
951425a6-476d-4b80-b2a5-fc689faf9793  13.366110  48.589720   
dfbcb1cf-0bf1-4d03-be32-eb2fd463a7fc   9.194154  48.807537   
53f0c29d-1c15-4fbf-84f6-4bbb48b65e2e   8.854977  49.893199   
10ddac26-a5ba-453d-a761-9ad2f041b2b8  11.379397  50.493148   
dfa29b2c-33b4-4a87-be3e-164512e663e8   8.833537  49.710188   

                                      44e2bdb7-13e3-4156-8576-8326cdd20459   
uuid                                                                         
64d12df3-2339-4d01-87a5-730663b6e9d5                            234.762797  \
64d208c2-6e07-48eb-8824-1237ab1a3ab3                            263.709650   
dfe3bd39-83cd-43b9-8628-f09896331b19                            216.526665   
10dbb42c-f2bb-5985-9dad-fbce82794a46                            305.950535   
dfcd38b3-602f-4d88-bb2f-f169c7176ea6                            193.233784   
64d9e72f-6327-4257-98bd-d0fbe75d4eee                            227.273106   
951425a6-476d-4b80-b2a5-fc689faf9793                            379.789289   
dfbcb1cf-0bf1-4d03-be32-eb2fd463a7fc                            216.301244   
53f0c29d-1c15-4fbf-84f6-4bbb48b65e2e                            100.128006   
10ddac26-a5ba-453d-a761-9ad2f041b2b8                            150.934033   
dfa29b2c-33b4-4a87-be3e-164512e663e8                            120.100550   

                                      ad812258-94e7-473d-aa80-d392f7532218   
uuid                                                                         
64d12df3-2339-4d01-87a5-730663b6e9d5                            315.035947  \
64d208c2-6e07-48eb-8824-1237ab1a3ab3                            294.299071   
dfe3bd39-83cd-43b9-8628-f09896331b19                            259.793423   
10dbb42c-f2bb-5985-9dad-fbce82794a46                            364.646364   
dfcd38b3-602f-4d88-bb2f-f169c7176ea6                            310.837399   
64d9e72f-6327-4257-98bd-d0fbe75d4eee                            278.536074   
951425a6-476d-4b80-b2a5-fc689faf9793                            505.350959   
dfbcb1cf-0bf1-4d03-be32-eb2fd463a7fc                            256.441040   
53f0c29d-1c15-4fbf-84f6-4bbb48b65e2e                            150.806775   
10ddac26-a5ba-453d-a761-9ad2f041b2b8                            299.854663   
dfa29b2c-33b4-4a87-be3e-164512e663e8                            162.704214   

                                      0e18d0d3-ed38-4e7f-a18e-507a78ad901d   
uuid                                                                         
64d12df3-2339-4d01-87a5-730663b6e9d5                            104.587372  \
64d208c2-6e07-48eb-8824-1237ab1a3ab3                            577.316838   
dfe3bd39-83cd-43b9-8628-f09896331b19                            175.831086   
10dbb42c-f2bb-5985-9dad-fbce82794a46                            596.912562   
dfcd38b3-602f-4d88-bb2f-f169c7176ea6                            141.531791   
64d9e72f-6327-4257-98bd-d0fbe75d4eee                            155.396997   
951425a6-476d-4b80-b2a5-fc689faf9793                            147.857161   
dfbcb1cf-0bf1-4d03-be32-eb2fd463a7fc                            180.983277   
53f0c29d-1c15-4fbf-84f6-4bbb48b65e2e                            268.940402   
10ddac26-a5ba-453d-a761-9ad2f041b2b8                            257.200242   
dfa29b2c-33b4-4a87-be3e-164512e663e8                            256.371960   

                                      e1a15081-24d1-9107-e040-0b0a3dfe563c   
uuid                                                                         
64d12df3-2339-4d01-87a5-730663

In [77]:
station_distances.head()

longitude  latitude   
uuid                                                        
44e2bdb7-13e3-4156-8576-8326cdd20459        0.0       0.0  \
ad812258-94e7-473d-aa80-d392f7532218        0.0       0.0   
0e18d0d3-ed38-4e7f-a18e-507a78ad901d        0.0       0.0   
e1a15081-24d1-9107-e040-0b0a3dfe563c        0.0       0.0   
e1a15081-24d0-9107-e040-0b0a3dfe563c        0.0       0.0   

                                      44e2bdb7-13e3-4156-8576-8326cdd20459   
uuid                                                                         
44e2bdb7-13e3-4156-8576-8326cdd20459                                   0.0  \
ad812258-94e7-473d-aa80-d392f7532218                                   0.0   
0e18d0d3-ed38-4e7f-a18e-507a78ad901d                                   0.0   
e1a15081-24d1-9107-e040-0b0a3dfe563c                                   0.0   
e1a15081-24d0-9107-e040-0b0a3dfe563c                                   0.0   

                                      ad812258-94e7-473d-aa80-d392f7532218   
uuid                                                                         
44e2bdb7-13e3-4156-8576-8326cdd20459                                   0.0  \
ad812258-94e7-473d-aa80-d392f7532218                                   0.0   
0e18d0d3-ed38-4e7f-a18e-507a78ad901d                                   0.0   
e1a15081-24d1-9107-e040-0b0a3dfe563c                                   0.0   
e1a15081-24d0-9107-e040-0b0a3dfe563c                                   0.0   

                                      0e18d0d3-ed38-4e7f-a18e-507a78ad901d   
uuid                                                                         
44e2bdb7-13e3-4156-8576-8326cdd20459                                   0.0  \
ad812258-94e7-473d-aa80-d392f7532218                                   0.0   
0e18d0d3-ed38-4e7f-a18e-507a78ad901d                                   0.0   
e1a15081-24d1-9107-e040-0b0a3dfe563c                                   0.0   
e1a15081-24d0-9107-e040-0b0a3dfe563c                                   0.0   

                                      e1a15081-24d1-9107-e040-0b0a3dfe563c   
uuid                                                                         
44e2bdb7-13e3-4156-8576-8326cdd20459                                   0.0  \
ad812258-94e7-473d-aa80-d392f7532218                                   0.0   
0e18d0d3-ed38-4e7f-a18e-507a78ad901d                                   0.0   
e1a15081-24d1-9107-e040-0b0a3dfe563c                                   0.0   
e1a15081-24d0-9107-e040-0b0a3dfe563c                                   0.0   

                                      e1a15081-24d0-9107-e040-0b0a3dfe563c   
uuid                                                                         
44e2bdb7-13e3-4156-8576-8326cdd20459                                   0.0  \
ad812258-94e7-473d-aa80-d392f7532218                                   0.0   
0e18d0d3-ed38-4e7f-a18e-507a78ad901d                                   0.0   
e1a15081-24d1-9107-e040-0b0a3dfe563c                                   0.0   
e1a15081-24d0-9107-e040-0b0a3dfe563c                                   0.0   

                                      e1a15081-24d3-9107-e040-0b0a3dfe563c   
uuid                                                                         
44e2bdb7-13e3-4156-8576-8326cdd20459                                   0.0  \
ad812258-94e7-473d-aa80-d392f7532218                                   0.0   
0e18d0d3-ed38-4e7f-a18e-507a78ad901d                                   0.0   
e1a15081-24d1-9107-e040-0b0a3dfe563c                                   0.0   
e1a15081-24d0-9107-e040-0b0a3dfe563c                                   0.0   

                                      e1a15081-24cd-9107-e040-0b0a3dfe563c   
uuid                                                                         
44e2bdb7-13e3-4156-8576-8326cdd20459                                   0.0  \
ad812258-94e7-473d-aa80-d392f7532218                                   0.0   
0e18d0d3-ed38-4e

In [30]:
station_list.info()

<class 'pandas.core.frame.DataFrame'>
Index: 168775 entries, 0 to 16874
Data columns (total 12 columns):
 #   Column             Non-Null Count   Dtype         
---  ------             --------------   -----         
 0   uuid               168775 non-null  object        
 1   name               168765 non-null  object        
 2   brand              161725 non-null  object        
 3   street             168755 non-null  object        
 4   house_number       158750 non-null  object        
 5   post_code          168765 non-null  object        
 6   city               168735 non-null  object        
 7   latitude           168775 non-null  float64       
 8   longitude          168775 non-null  float64       
 9   first_active       168775 non-null  object        
 10  openingtimes_json  168775 non-null  object        
 11  file_date          168775 non-null  datetime64[ns]
dtypes: datetime64[ns](1), float64(2), object(9)
memory usage: 16.7+ MB


## Station Duplicates with differing lat / lon 

In [31]:
station_dups = station_location.copy()
station_dups.drop_duplicates(inplace=True)

In [32]:
print("Shape: " + str(station_dups.shape))
print("Unique values: " + str(station_dups.nunique()))

Shape: (16885, 3)
Unique values: uuid         16885
longitude    16612
latitude     16566
dtype: int64


In [33]:
location_info = station_dups[station_dups.duplicated(['uuid'])].sort_values("uuid")
location_info["uuid"].head(20)

Series([], Name: uuid, dtype: object)

In [34]:
dup_uuids = location_info["uuid"].to_list()

station_dups.query("uuid in @dup_uuids").sort_values("uuid")

Empty DataFrame
Columns: [uuid, longitude, latitude]
Index: []

In [35]:
px.scatter_mapbox(station_dups.query("uuid in @dup_uuids"), 
                  lat="latitude", 
                  lon="longitude", 
                  mapbox_style="open-street-map",
                  color_discrete_sequence=["fuchsia"],
                  height=800)